In [6]:
"""
Vietnamese URL Scraper for Common Crawl.

This script queries the Common Crawl Index API (CDXJ) to retrieve metadata
for URLs ending in '.vn'. It paginates through the index results,
deduplicates findings, and saves the URLs, WARC filenames, and offsets
to a CSV file for future processing.

Outputs:
    - vi_commoncrawl_urls.csv: A CSV containing unique Vietnamese URLs
      with their respective WARC storage details.
"""

import requests
import json
import pandas as pd
from tqdm import tqdm
import logging
import time

logging.basicConfig(level=logging.INFO, format="%(asctime)s - %(message)s")
logger = logging.getLogger(__name__)

OUTPUT_FILE = "vi_commoncrawl_urls.csv"
MAX_URLS = 50_000
INDEX_NAME = "CC-MAIN-2025-51-index"
BASE_URL = f"https://index.commoncrawl.org/{INDEX_NAME}"
urls = []

page = 0
while len(urls) < MAX_URLS:
    try:
        logger.info(f"Fetching page {page}…")
        params = {
            "url": "*.vn/*",
            "output": "json",
            "page": page
        }
        resp = requests.get(BASE_URL, params=params, timeout=30)
        if resp.status_code != 200 or not resp.text.strip():
            logger.info(f"No more results at page {page}")
            break

        lines = resp.text.strip().split("\n")
        count_before = len(urls)
        for line in lines:
            try:
                rec = json.loads(line)
                urls.append({
                    "url": rec["url"],
                    "warc_filename": rec["filename"],
                    "offset": rec["offset"],
                    "length": rec["length"]
                })
            except Exception:
                continue

        logger.info(f"Collected {len(urls)} URLs so far")
        if len(urls) == count_before:
            # No new URLs found means likely pagination ended
            break

        page += 1
        time.sleep(1)  # politeness delay between pages

    except Exception as e:
        logger.warning(f"[ERROR] Request failed on page {page}: {e}")
        time.sleep(5)
        continue

df = pd.DataFrame(urls).drop_duplicates(subset="url").head(MAX_URLS)
df.to_csv(OUTPUT_FILE, index=False)
logger.info(f"Done! Saved {len(df)} Vietnamese URLs to {OUTPUT_FILE}")



2026-01-24 14:51:46,499 - Fetching page 0…
2026-01-24 14:51:54,977 - Collected 12417 URLs so far
2026-01-24 14:51:55,982 - Fetching page 1…
2026-01-24 14:52:04,725 - Collected 27417 URLs so far
2026-01-24 14:52:05,730 - Fetching page 2…
2026-01-24 14:52:13,563 - Collected 42417 URLs so far
2026-01-24 14:52:14,567 - Fetching page 3…
2026-01-24 14:52:24,232 - Collected 57417 URLs so far
2026-01-24 14:52:25,780 - ✅ Done! Saved 50000 Vietnamese URLs to vi_commoncrawl_urls.csv


In [1]:
"""
Common Crawl WARC Downloader & Text Extractor.

This script processes a list of Common Crawl metadata to download raw HTML
and convert it into clean text. It uses multi-threading to handle high-latency
requests and I/O operations efficiently.

Workflow:
    1. Reads URL metadata (offset, length, filename) from a local CSV.
    2. Fetches specific WARC records using HTTP Range requests.
    3. Extracts raw HTML and saves it to 'vi_html/'.
    4. Parses HTML with BeautifulSoup (lxml) to remove scripts/styles.
    5. Saves cleaned text files to 'vi_text/'.

Configuration:
    - Threading: Controlled by MAX_THREADS (default: 20).
    - Batching: Processes URLs in chunks (BATCH_SIZE) to manage memory.

The code here has issues with URLs sharing the same first 60 characters and hence we used the code below for our data collection instead.
"""

import pandas as pd
import requests
import io
from pathlib import Path
from warcio.archiveiterator import ArchiveIterator
from bs4 import BeautifulSoup
import logging
from concurrent.futures import ThreadPoolExecutor, as_completed
import time

# -------------------------------
# CONFIG
# -------------------------------
URL_CSV = "vi_commoncrawl_urls.csv"
HTML_DIR = Path("vi_html")
TEXT_DIR = Path("vi_text")
HTML_DIR.mkdir(exist_ok=True)
TEXT_DIR.mkdir(exist_ok=True)
MAX_THREADS = 20
MAX_RETRIES = 3
BATCH_SIZE = 1000  # split URLs into manageable chunks

logging.basicConfig(level=logging.INFO, format="%(asctime)s - %(message)s")
logger = logging.getLogger(__name__)

# -------------------------------
# HELPERS
# -------------------------------
def fetch_html(row):
    url = row["url"]
    warc_path = row["warc_filename"]
    offset = int(row["offset"])
    length = int(row["length"])
    if "crawldiagnostics" in warc_path.lower():
        logger.info(f"⏭️ Skipping diagnostic WARC for {url}")
        return None

    http_url = f"https://data.commoncrawl.org/{warc_path}"
    headers = {"Range": f"bytes={offset}-{offset + length - 1}"}
    safe_name = "".join(c if c.isalnum() else "_" for c in url[:60]) + ".html"
    output_path = HTML_DIR / safe_name

    if output_path.exists():
        return output_path

    for attempt in range(MAX_RETRIES):
        try:
            resp = requests.get(http_url, headers=headers, timeout=60)
            resp.raise_for_status()
            for record in ArchiveIterator(io.BytesIO(resp.content)):
                if record.rec_type == "response":
                    html = record.content_stream().read().decode("utf-8", errors="ignore")
                    output_path.write_text(html, encoding="utf-8")
                    logger.info(f"✅ Fetched {url}")
                    return output_path
        except Exception as e:
            logger.warning(f"⚠️ Attempt {attempt+1} failed for {url}: {e}")
            time.sleep(2)
    return None

def extract_text(html_file):
    try:
        html = html_file.read_text(encoding="utf-8", errors="ignore")
        soup = BeautifulSoup(html, "lxml")
        for script in soup(["script", "style"]):
            script.decompose()
        lines = [line.strip() for line in soup.get_text(separator="\n").splitlines() if line.strip()]
        clean_text = "\n".join(lines)
        txt_file = TEXT_DIR / (html_file.stem + ".txt")
        txt_file.write_text(clean_text, encoding="utf-8")
        logger.info(f"✅ Extracted {html_file.name}")
        return txt_file
    except Exception as e:
        logger.warning(f"⚠️ Failed to extract {html_file.name}: {e}")
        return None

# -------------------------------
# MAIN
# -------------------------------
df = pd.read_csv(URL_CSV)
logger.info(f"Loaded {len(df)} URLs from {URL_CSV}")

# Split into batches to avoid overloading threads
for start in range(0, len(df), BATCH_SIZE):
    batch = df.iloc[start:start+BATCH_SIZE]
    logger.info(f"Processing batch {start} to {start + len(batch)}")

    # ---- Fetch HTML ----
    html_files = []
    with ThreadPoolExecutor(max_workers=MAX_THREADS) as executor:
        futures = [executor.submit(fetch_html, row) for _, row in batch.iterrows()]
        for future in as_completed(futures):
            result = future.result()
            if result:
                html_files.append(result)

    logger.info(f"✅ Downloaded {len(html_files)} HTML files in this batch")

    # ---- Extract text ----
    with ThreadPoolExecutor(max_workers=MAX_THREADS) as executor:
        futures = [executor.submit(extract_text, html_file) for html_file in html_files]
        for future in as_completed(futures):
            _ = future.result()

logger.info(f"🎉 All done! Text files are in {TEXT_DIR}")


2026-01-24 16:34:22,398 - Loaded 50000 URLs from vi_commoncrawl_urls.csv
2026-01-24 16:34:22,401 - Processing batch 0 to 1000
2026-01-24 16:34:22,448 - ⏭️ Skipping diagnostic WARC for https://028.vn/bat-dong-san/chinh-chu-can-ban-ha-trng-tam-da-nang-35195.html
2026-01-24 16:34:22,449 - ⏭️ Skipping diagnostic WARC for https://028.vn/cac-loai-hinh-khac/bang-gia-kham-nam-khoa-tai-binh-duong-chi-phi-cu-the-cho-tung-hang-muc-34856.html
2026-01-24 16:34:22,461 - ⏭️ Skipping diagnostic WARC for https://028.vn/cac-loai-hinh-khac/bo-mat-na-phong-doc-vian-620p-34870.html
2026-01-24 16:34:22,472 - ⏭️ Skipping diagnostic WARC for https://028.vn/cac-loai-hinh-khac/cau-truot-tre-em-xich-du-tre-em-du-quay-tre-em-nhap-khau-34853.html
2026-01-24 16:34:22,483 - ⏭️ Skipping diagnostic WARC for https://028.vn/cac-loai-hinh-khac/cua-cach-nhiet-lua-chon-thong-minh-cho-nha-o-va-cong-trinh-xanh-34850.html
2026-01-24 16:34:22,484 - ⏭️ Skipping diagnostic WARC for https://028.vn/cac-loai-hinh-khac/cua-go-ho-chi

In [ ]:
"""
Common Crawl Downloader & Extractor (Optimized for I/O).

This script handles large-scale data retrieval and processing. It is specifically
architected to bypass Python's Global Interpreter Lock (GIL) limitations.

Threading Strategy:
    - Network I/O: Threading is used for 'requests.get' because the GIL is
      released while waiting for the Common Crawl server to respond.
    - Disk I/O: The GIL is released during 'write_text' and 'read_text' calls,
      allowing multiple files to be saved/loaded concurrently.
    - Resume Logic: Identifies missing files via SHA-1 hashes before execution
       to ensure the script is idempotent.

Dependencies:
    - warcio: For stream-parsing WARC records.
    - BeautifulSoup: For HTML-to-text conversion.
"""

import pandas as pd
import requests
import io
from pathlib import Path
from warcio.archiveiterator import ArchiveIterator
from bs4 import BeautifulSoup
import logging
from concurrent.futures import ThreadPoolExecutor, as_completed
import time
import hashlib

# -------------------------------
# CONFIG
# -------------------------------
URL_CSV = "vi_commoncrawl_urls.csv"
HTML_DIR = Path("vi_html")
TEXT_DIR = Path("vi_text")
HTML_DIR.mkdir(exist_ok=True)
TEXT_DIR.mkdir(exist_ok=True)
MAX_THREADS = 20
MAX_RETRIES = 3
BATCH_SIZE = 1000  # split URLs into manageable chunks

logging.basicConfig(level=logging.INFO, format="%(asctime)s - %(message)s")
logger = logging.getLogger(__name__)


# -------------------------------
# HELPERS
# -------------------------------
def url_to_filename(url: str) -> str:
    """Generate a unique filename for a URL using a hash."""
    h = hashlib.sha1(url.encode()).hexdigest()[:12]  # 12 hex chars
    safe = "".join(c if c.isalnum() else "_" for c in url[:30])  # first 30 chars safe
    return f"{safe}_{h}.html"


def fetch_html(row):
    url = row["url"]
    warc_path = row["warc_filename"]
    offset = int(row["offset"])
    length = int(row["length"])
    if "crawldiagnostics" in warc_path.lower():
        logger.info(f"⏭️ Skipping diagnostic WARC for {url}")
        return None

    http_url = f"https://data.commoncrawl.org/{warc_path}"
    headers = {"Range": f"bytes={offset}-{offset + length - 1}"}
    safe_name = url_to_filename(url)
    output_path = HTML_DIR / safe_name

    if output_path.exists():
        return output_path

    for attempt in range(MAX_RETRIES):
        try:
            resp = requests.get(http_url, headers=headers, timeout=60)
            resp.raise_for_status()
            for record in ArchiveIterator(io.BytesIO(resp.content)):
                if record.rec_type == "response":
                    html = record.content_stream().read().decode("utf-8", errors="ignore")
                    output_path.write_text(html, encoding="utf-8")
                    logger.info(f"✅ Fetched {url}")
                    return output_path
        except Exception as e:
            logger.warning(f"⚠️ Attempt {attempt + 1} failed for {url}: {e}")
            time.sleep(2)
    return None


def extract_text(html_file):
    try:
        html = html_file.read_text(encoding="utf-8", errors="ignore")
        soup = BeautifulSoup(html, "lxml")
        for script in soup(["script", "style"]):
            script.decompose()
        lines = [line.strip() for line in soup.get_text(separator="\n").splitlines() if line.strip()]
        clean_text = "\n".join(lines)
        txt_file = TEXT_DIR / (html_file.stem + ".txt")
        txt_file.write_text(clean_text, encoding="utf-8")
        logger.info(f"✅ Extracted {html_file.name}")
        return txt_file
    except Exception as e:
        logger.warning(f"⚠️ Failed to extract {html_file.name}: {e}")
        return None


# -------------------------------
# MAIN
# -------------------------------
df = pd.read_csv(URL_CSV)
logger.info(f"Loaded {len(df)} URLs from {URL_CSV}")

# Determine which URLs are missing (resume-safe)
existing_files = set(p.name for p in HTML_DIR.glob("*.html"))
missing_df = df[df.apply(lambda row: url_to_filename(row["url"]) not in existing_files, axis=1)]
logger.info(f"{len(missing_df)} URLs remaining to fetch")

for start in range(0, len(missing_df), BATCH_SIZE):
    batch = missing_df.iloc[start:start + BATCH_SIZE]
    logger.info(f"Processing batch {start} to {start + len(batch)}")

    # ---- Fetch HTML ----
    html_files = []
    with ThreadPoolExecutor(max_workers=MAX_THREADS) as executor:
        futures = [executor.submit(fetch_html, row) for _, row in batch.iterrows()]
        for future in as_completed(futures):
            result = future.result()
            if result:
                html_files.append(result)

    logger.info(f"✅ Downloaded {len(html_files)} HTML files in this batch")

    # ---- Extract text ----
    with ThreadPoolExecutor(max_workers=MAX_THREADS) as executor:
        futures = [executor.submit(extract_text, html_file) for html_file in html_files]
        for future in as_completed(futures):
            _ = future.result()

logger.info(f"🎉 All done! Text files are in {TEXT_DIR}")


2026-01-25 17:28:20,140 - Loaded 50000 URLs from vi_commoncrawl_urls.csv
2026-01-25 17:28:31,912 - 50000 URLs remaining to fetch
2026-01-25 17:28:35,165 - Processing batch 0 to 1000
2026-01-25 17:28:39,309 - ✅ Fetched http://0101.vn/robots.txt
2026-01-25 17:28:39,336 - ✅ Fetched http://0101.vn/Downloads.aspx?cat=7
2026-01-25 17:28:39,353 - ✅ Fetched https://007studio.vn/index.php/2023/12/17/man-restaurant/
2026-01-25 17:28:39,354 - ✅ Fetched http://0101.vn/Downloads.aspx?cat=9
2026-01-25 17:28:39,355 - ✅ Fetched http://0101.vn/ShowArticle.aspx?ID=1025
2026-01-25 17:28:39,355 - ✅ Fetched http://0101.vn/
2026-01-25 17:28:39,356 - ✅ Fetched http://0101.vn/Downloads.aspx?cat=1
2026-01-25 17:28:39,356 - ✅ Fetched https://007studio.vn/index.php/2023/12/17/viet-duc-showroom/
2026-01-25 17:28:39,356 - ✅ Fetched http://0101.vn/Downloads.aspx?cat=8
2026-01-25 17:28:39,357 - ✅ Fetched http://0101.vn/Default.aspx
2026-01-25 17:28:39,357 - ✅ Fetched http://0101.vn/Downloads.aspx?cat=5
2026-01-25 17

In [1]:
from datasets import load_dataset
from urllib.parse import urlparse
import pandas as pd
from pathlib import Path
from tqdm import tqdm  # optional visual progress

# ────────────────────────────────────────────────
# Configuration
# ────────────────────────────────────────────────
TARGET_COUNT       = 200_000          # adjust as needed
OUTPUT_CSV         = Path("data/vi_mc4_urls.csv")
FILTER_NON_VN      = True             # exclude .vn domains for diversity
MIN_TEXT_LENGTH    = 200              # skip very short documents

# ────────────────────────────────────────────────
# Load streaming dataset (no full download)
# ────────────────────────────────────────────────
print("Loading streaming Vietnamese mC4 subset...")
ds = load_dataset(
    "allenai/c4",
    "vi",                     # or "multilingual" + manual lang filter if needed
    split="train",
    streaming=True,
    trust_remote_code=True    # sometimes required for older configs
)

# ────────────────────────────────────────────────
# Collect URLs with basic filtering
# ────────────────────────────────────────────────
collected = []
domain_counts = {}  # optional: track TLD diversity

print("Collecting URLs...")
for example in tqdm(ds, desc="Processing examples"):
    url = example["url"].strip()
    text = example["text"].strip()

    if len(text) < MIN_TEXT_LENGTH:
        continue

    domain = urlparse(url).netloc.lower()

    if FILTER_NON_VN and domain.endswith(".vn"):
        continue

    collected.append({
        "url": url,
        "domain": domain,
        "text_length": len(text),
        "timestamp": example.get("timestamp", "")
    })

    # Optional: track domain stats
    tld = "." + domain.split(".")[-1]
    domain_counts[tld] = domain_counts.get(tld, 0) + 1

    if len(collected) >= TARGET_COUNT:
        break

# ────────────────────────────────────────────────
# Save & summarize
# ────────────────────────────────────────────────
if collected:
    df = pd.DataFrame(collected)
    df = df.drop_duplicates(subset="url")
    df.to_csv(OUTPUT_CSV, index=False)

    print(f"\nDone! Collected and saved {len(df):,} unique URLs")
    print(f"Output → {OUTPUT_CSV.resolve()}")

    if domain_counts:
        print("\nTop TLD distribution (for diversity check):")
        print(pd.Series(domain_counts).sort_values(ascending=False).head(12))
else:
    print("No documents collected – check connectivity or filters.")

/Users/restaurantalsheika/miniconda3/envs/graph-aware-phishing-commoncrawl/lib/python3.10/site-packages/tqdm/auto.py:21: TqdmWarning: IProgress not found. Please update jupyter and ipywidgets. See https://ipywidgets.readthedocs.io/en/stable/user_install.html
  from .autonotebook import tqdm as notebook_tqdm
`trust_remote_code` is not supported anymore.
Please check that the Hugging Face dataset 'allenai/c4' isn't based on a loading script and remove `trust_remote_code`.
If the dataset is based on a loading script, please ask the dataset author to remove it and convert it to a standard format like Parquet.


Loading streaming Vietnamese mC4 subset...


Processing examples: 403841it [04:04, 1651.24it/s]



Done! Collected and saved 200,000 unique URLs
Output → /Users/restaurantalsheika/graph-aware-phishing-commoncrawl/notebooks/data/vi_mc4_urls.csv

Top TLD distribution (for diversity check):
.com       134041
.net        30193
.org        12200
.info        6044
.tv          1646
.cn          1128
.biz         1013
.ru           805
.co           700
.online       647
.xyz          642
.us           638
dtype: int64


In [2]:
import os
from pathlib import Path

csv_path = Path("/Users/restaurantalsheika/graph-aware-phishing-commoncrawl/notebooks/data/vi_mc4_urls.csv")

print("Does the file exist?", csv_path.exists())
print("Is it a file?", csv_path.is_file())
print("Absolute path:", csv_path.resolve())
print("Parent directory exists?", csv_path.parent.exists())
print("Files in parent directory:", list(csv_path.parent.glob("*")))

Does the file exist? True
Is it a file? True
Absolute path: /Users/restaurantalsheika/graph-aware-phishing-commoncrawl/notebooks/data/vi_mc4_urls.csv
Parent directory exists? True
Files in parent directory: [PosixPath('/Users/restaurantalsheika/graph-aware-phishing-commoncrawl/notebooks/data/safe'), PosixPath('/Users/restaurantalsheika/graph-aware-phishing-commoncrawl/notebooks/data/vi_non_vn_urls_summary.txt'), PosixPath('/Users/restaurantalsheika/graph-aware-phishing-commoncrawl/notebooks/data/vi_mc4_urls.csv')]


In [10]:
import pandas as pd
from pathlib import Path
from urllib.parse import urlparse
from datasets import load_dataset
from tqdm import tqdm

# ────────────────────────────────────────────────
# Configuration
# ────────────────────────────────────────────────
EXISTING_CSV     = Path("data/vi_mc4_urls.csv")
NEW_CSV          = Path("data/vi_mc4_additional_urls.csv")
TARGET_NEW_URLS  = 500_000          # aim for 500k new URLs → expect 45–100k successful HTML later
MIN_TEXT_LENGTH  = 400
FILTER_NON_VN    = True

# ────────────────────────────────────────────────
# Load existing URLs into a set for fast lookup
# ────────────────────────────────────────────────
print("Loading existing URLs for deduplication...")
if EXISTING_CSV.is_file():
    df_existing = pd.read_csv(EXISTING_CSV, usecols=["url"])
    existing_urls = set(df_existing["url"].dropna().str.strip())
    print(f"Loaded {len(existing_urls):,} unique URLs from existing file")
else:
    existing_urls = set()
    print("No existing file found → no deduplication will be applied")

# ────────────────────────────────────────────────
# Stream additional documents from mC4 Vietnamese subset
# ────────────────────────────────────────────────
print("\nStreaming additional documents from allenai/c4 'vi' subset...")
ds = load_dataset("allenai/c4", "vi", split="train", streaming=True)

collected = []
skipped_existing = 0
skipped_short    = 0
skipped_vn       = 0

print("Collecting new URLs (estimated time: 15–60 minutes depending on network and filtering)...")

for example in tqdm(ds, desc="Processing mC4 documents", unit="doc"):
    text = example.get("text", "").strip()
    if len(text) < MIN_TEXT_LENGTH:
        skipped_short += 1
        continue

    url = example.get("url", "").strip()
    if not url:
        continue

    # Skip if already in the existing collection
    if url in existing_urls:
        skipped_existing += 1
        continue

    domain = urlparse(url).netloc.lower()
    if FILTER_NON_VN and domain.endswith(".vn"):
        skipped_vn += 1
        continue

    collected.append({
        "url": url,
        "domain": domain,
        "text_length": len(text),
        "timestamp": example.get("timestamp", ""),
    })

    if len(collected) >= TARGET_NEW_URLS:
        break

# ────────────────────────────────────────────────
# Save the new collection
# ────────────────────────────────────────────────
if collected:
    df_new = pd.DataFrame(collected).drop_duplicates(subset="url")
    df_new.to_csv(NEW_CSV, index=False)

    print("\n" + "═" * 70)
    print("Collection complete")
    print(f"New unique URLs saved:          {len(df_new):,}")
    print(f"Skipped (already in existing):  {skipped_existing:,}")
    print(f"Skipped (text too short):       {skipped_short:,}")
    print(f"Skipped (.vn domains):          {skipped_vn:,}")
    print(f"File written → {NEW_CSV.resolve()}")

    print("\nTop 12 domains in new collection:")
    print(df_new["domain"].value_counts().head(12))
else:
    print("No new URLs collected after applying filters.")

Loading existing URLs for deduplication...
Loaded 200,000 unique URLs from existing file

Streaming additional documents from allenai/c4 'vi' subset...



Processing mC4 documents: 0doc [00:00, ?doc/s]
Processing mC4 documents: 1doc [00:04,  4.27s/doc]
Processing mC4 documents: 906doc [00:04, 293.13doc/s]
Processing mC4 documents: 1552doc [00:04, 533.84doc/s]
Processing mC4 documents: 2980doc [00:04, 1306.39doc/s]
Processing mC4 documents: 3792doc [00:05, 1089.51doc/s]
Processing mC4 documents: 4598doc [00:06, 1255.80doc/s]
Processing mC4 documents: 5442doc [00:06, 1733.58doc/s]
Processing mC4 documents: 6002doc [00:06, 2020.54doc/s]
Processing mC4 documents: 6524doc [00:07, 1195.96doc/s]
Processing mC4 documents: 6899doc [00:07, 1110.10doc/s]
Processing mC4 documents: 7374doc [00:07, 1387.61doc/s]
Processing mC4 documents: 7715doc [00:08, 1582.51doc/s]
Processing mC4 documents: 8053doc [00:08, 1136.93doc/s]
Processing mC4 documents: 8556doc [00:08, 1507.75doc/s]
Processing mC4 documents: 8869doc [00:08, 1605.81doc/s]
Processing mC4 documents: 9308doc [00:09, 969.17doc/s] 
Processing mC4 documents: 9995doc [00:09, 1497.81doc/s]
Processi


══════════════════════════════════════════════════════════════════════
Collection complete
New unique URLs saved:          500,000
Skipped (already in existing):  183,238
Skipped (text too short):       220,674
Skipped (.vn domains):          602,484
File written → /Users/restaurantalsheika/graph-aware-phishing-commoncrawl/notebooks/data/vi_mc4_additional_urls.csv

Top 12 domains in new collection:
domain
123doc.org                3228
vnexpress.net             2655
bachhoa24.com             2195
www.baomoi.com            2069
vi.wikipedia.org          1827
vietnamese.alibaba.com    1801
timdat.net                1785
truyenyy.com              1640
vietgiaitri.com           1614
m.baomoi.com              1610
www.ivivu.com             1526
vatgia.com                1460
Name: count, dtype: int64


In [6]:
import asyncio
import aiohttp
import aiofiles
import hashlib
from pathlib import Path
from urllib.parse import urlparse
import pandas as pd
from tqdm.asyncio import tqdm_asyncio
from tenacity import retry, stop_after_attempt, wait_exponential, retry_if_exception_type
from aiohttp import ClientError, ClientConnectorError, ClientResponseError, ClientTimeout, ClientConnectorCertificateError

# ────────────────────────────────────────────────
# Configuration
# ────────────────────────────────────────────────
CSV_PATH         = Path("data/vi_mc4_urls.csv")
HTML_DIR         = Path("data/html_mc4_current")
HTML_DIR.mkdir(exist_ok=True, parents=True)

MAX_CONCURRENT   = 25                # conservative starting value
REQUEST_TIMEOUT  = aiohttp.ClientTimeout(total=45)
MAX_RETRIES      = 5                 # per URL
BATCH_SIZE       = 2000              # adjust as needed
POLITENESS_DELAY = 1.5               # seconds between batches

USER_AGENT = (
    "Mozilla/5.0 (Windows NT 10.0; Win64; x64) "
    "AppleWebKit/537.36 (KHTML, like Gecko) "
    "Chrome/122.0.0.0 Safari/537.36"
)

# ────────────────────────────────────────────────
# Retry decorator (certificate errors are included)
# ────────────────────────────────────────────────
@retry(
    stop=stop_after_attempt(MAX_RETRIES),
    wait=wait_exponential(multiplier=1.2, min=3, max=60),
    retry=retry_if_exception_type((
        ClientError,
        ClientConnectorError,
        ClientResponseError,
        ClientTimeout,
        ClientConnectorCertificateError
    )),
    reraise=True
)
async def fetch_single(session: aiohttp.ClientSession, url: str) -> tuple[Path | None, str]:
    headers = {"User-Agent": USER_AGENT}
    async with session.get(
        url,
        headers=headers,
        timeout=REQUEST_TIMEOUT,
        allow_redirects=True
        # No ssl=False — full verification
    ) as resp:
        if resp.status != 200:
            return None, url
        html_bytes = await resp.read()
        domain_hash = hashlib.sha256(url.encode()).hexdigest()[:12]
        safe_name = f"{urlparse(url).netloc.replace('.', '_')}_{domain_hash}.html"
        path = HTML_DIR / safe_name
        async with aiofiles.open(path, "wb") as f:
            await f.write(html_bytes)
        return path, url

# ────────────────────────────────────────────────
# Batch processor — continues even if individual tasks fail
# ────────────────────────────────────────────────
async def process_batch(urls: list[str]):
    connector = aiohttp.TCPConnector(limit=MAX_CONCURRENT)
    async with aiohttp.ClientSession(connector=connector) as session:
        tasks = [fetch_single(session, url) for url in urls]
        results = []
        failures = []

        for coro in tqdm_asyncio.as_completed(tasks, desc=f"Fetching {len(urls)} URLs"):
            try:
                result = await coro
                results.append(result)
            except Exception as exc:
                # Capture the URL and exception for reporting
                # (We know which future failed by matching, but for simplicity we log here)
                failed_url = "unknown"  # improved tracking requires more bookkeeping
                failures.append((failed_url, exc))
                results.append((None, failed_url))

        success = sum(1 for r, _ in results if r is not None)
        if failures:
            print(f"Batch had {len(failures)} failures after retries:")
            for url, exc in failures[:5]:  # show first 5 only
                print(f"  • {url}: {type(exc).__name__} – {exc}")
            if len(failures) > 5:
                print(f"  … and {len(failures)-5} more")

        print(f"Batch complete → {success:,} successful / {len(urls):,} attempted")
        return success

# ────────────────────────────────────────────────
# Main orchestrator
# ────────────────────────────────────────────────
async def main_fetch():
    df = pd.read_csv(CSV_PATH)
    all_urls = df["url"].dropna().tolist()
    print(f"Total unique URLs to fetch: {len(all_urls):,}")

    total_success = 0
    for i in range(0, len(all_urls), BATCH_SIZE):
        batch_urls = all_urls[i:i + BATCH_SIZE]
        print(f"\nStarting batch {i // BATCH_SIZE + 1} ({len(batch_urls)} URLs)")
        success = await process_batch(batch_urls)
        total_success += success

        if i + BATCH_SIZE < len(all_urls):
            print(f"Pausing {POLITENESS_DELAY:.1f} seconds between batches...")
            await asyncio.sleep(POLITENESS_DELAY)

    print(f"\nFetching finished. Total successful HTML files: {total_success:,}")

# Execute in notebook context
await main_fetch()

Total unique URLs to fetch: 200,000

Starting batch 1 (2000 URLs)



Fetching 2000 URLs:   4%|▍         | 86/2000 [00:08<02:17, 13.90it/s]/Users/restaurantalsheika/miniconda3/envs/graph-aware-phishing-commoncrawl/lib/python3.10/concurrent/futures/_base.py:421: RuntimeWarning: coroutine 'fetch_batch' was never awaited
  with self._condition:

Fetching 2000 URLs: 100%|██████████| 2000/2000 [02:22<00:00, 14.06it/s]


Batch had 1684 failures after retries:
  • unknown: TimeoutError – 
  • unknown: TimeoutError – 
  • unknown: TimeoutError – 
  • unknown: TimeoutError – 
  • unknown: TimeoutError – 
  … and 1679 more
Batch complete → 208 successful / 2,000 attempted
Pausing 1.5 seconds between batches...

Starting batch 2 (2000 URLs)



Fetching 2000 URLs: 100%|██████████| 2000/2000 [01:12<00:00, 27.73it/s]


Batch had 1643 failures after retries:
  • unknown: TooManyRedirects – 0, message='', url='https://ione.net/lynk-lee-mac-vay-quet-dat-lan-dau-lam-vedette-4132629.html'
  • unknown: TimeoutError – 
  • unknown: TimeoutError – 
  • unknown: TimeoutError – 
  • unknown: TimeoutError – 
  … and 1638 more
Batch complete → 214 successful / 2,000 attempted
Pausing 1.5 seconds between batches...

Starting batch 3 (2000 URLs)


...

Batch had 1783 failures after retries:
  • unknown: TooManyRedirects – 0, message='', url='http://meyeucon.org/9704/y-nghia-cua-ten-nguoi-van-m/'
  • unknown: TimeoutError – 
  • unknown: TimeoutError – 
  • unknown: TimeoutError – 
  • unknown: TimeoutError – 
  … and 1778 more
Batch complete → 127 successful / 2,000 attempted
Pausing 1.5 seconds between batches...

Starting batch 99 (2000 URLs)



Fetching 2000 URLs: 100%|██████████| 2000/2000 [01:20<00:00, 24.89it/s]


Batch had 1703 failures after retries:
  • unknown: TimeoutError – 
  • unknown: TimeoutError – 
  • unknown: TimeoutError – 
  • unknown: TimeoutError – 
  • unknown: TimeoutError – 
  … and 1698 more
Batch complete → 167 successful / 2,000 attempted
Pausing 1.5 seconds between batches...

Starting batch 100 (2000 URLs)



Fetching 2000 URLs: 100%|██████████| 2000/2000 [01:32<00:00, 21.60it/s]


Batch had 1630 failures after retries:
  • unknown: ClientConnectorError – Cannot connect to host www.vncgarden.com:443 ssl:default [None]
  • unknown: ClientConnectorDNSError – Cannot connect to host winbetcasino.life:443 ssl:default [nodename nor servname provided, or not known]
  • unknown: TooManyRedirects – 0, message='', url='https://www.hanoisoundstuff.com/gia-vang-9999-o-thai-nguyen.html'
  • unknown: TimeoutError – 
  • unknown: TimeoutError – 
  … and 1625 more
Batch complete → 227 successful / 2,000 attempted

Fetching finished. Total successful HTML files: 18,464
